# APRIORI for Action Rules

### Data

In [1]:
import pandas as pd
transactions = {'Sex': ['M', 'F', 'M', 'M', 'F', 'M', 'F'], 
                'Age': ['Y', 'Y', 'O', 'Y', 'Y', 'O', 'Y'],
                'Class': [1, 1, 2, 2, 1, 1, 2],
                'Embarked': ['S', 'C', 'S', 'C', 'S', 'C', 'C'],
                'Survived': [1, 1, 0, 0, 1, 1, 0],
               }
data = pd.DataFrame.from_dict(transactions)
data

Sex Age  Class Embarked  Survived
0   M   Y      1        S         1
1   F   Y      1        C         1
2   M   O      2        S         0
3   M   Y      2        C         0
4   F   Y      1        S         1
5   M   O      1        C         1
6   F   Y      2        C         0

One Hot Encoding

In [2]:
#data = pd.get_dummies(data, sparse=True, columns=data.columns, prefix_sep='_<item>_')
data = pd.get_dummies(data, sparse=False, columns=data.columns, prefix_sep='_<item>_')
data

Sex_<item>_F  Sex_<item>_M  Age_<item>_O  Age_<item>_Y  Class_<item>_1  \
0             0             1             0             1               1   
1             1             0             0             1               1   
2             0             1             1             0               0   
3             0             1             0             1               0   
4             1             0             0             1               1   
5             0             1             1             0               1   
6             1             0             0             1               0   

   Class_<item>_2  Embarked_<item>_C  Embarked_<item>_S  Survived_<item>_0  \
0               0                  0                  1                  0   
1               0                  1                  0                  0   
2               1                  0                  1                  1   
3               1                  1                  0                  1   
4               0                  0                  1                  0   
5               0                  1                  0                  0   
6               1                  1                  0                  1   

   Survived_<item>_1  
0                  1  
1                  1  
2                  0  
3                  0  
4                  1  
5                  1  
6                  0

### Input parameters

In [3]:
stable_attributes = ['Sex','Age']
flexible_attributes = ['Class','Embarked']
target = 'Survived'
wanted_change_in_target = [0, 1]
min_stable_attributes = 2
min_flexible_attributes = 1 #min 1
min_unwanted_support = 1
min_unwanted_confidence = 0.5 #min 0.5
min_wanted_support = 2
min_wanted_confidence = 0.5 #min 0.5

### Bindings
Bind item columns with attributes

In [4]:
from collections import defaultdict

stable_items_binding = defaultdict(lambda: [])
flexible_items_binding = defaultdict(lambda: [])
target_items_binding = defaultdict(lambda: [])

for col in data.columns:
    is_continue = False
    # stable
    for attribute in stable_attributes:
        if col.startswith(attribute+'_<item>_'):
            stable_items_binding[attribute].append(col)
            is_continue = True
            break
    if is_continue is True:
        continue
    # flexible    
    for attribute in flexible_attributes:
        if col.startswith(attribute+'_<item>_'):
            flexible_items_binding[attribute].append(col)
            is_continue = True
            break
    if is_continue is True:
        continue
    # target    
    if col.startswith(target+'_<item>_'):
        target_items_binding[target].append(col)      

In [5]:
stable_items_binding  

defaultdict(<function __main__.<lambda>()>,
            {'Sex': ['Sex_<item>_F', 'Sex_<item>_M'],
             'Age': ['Age_<item>_O', 'Age_<item>_Y']})

In [6]:
flexible_items_binding 

defaultdict(<function __main__.<lambda>()>,
            {'Class': ['Class_<item>_1', 'Class_<item>_2'],
             'Embarked': ['Embarked_<item>_C', 'Embarked_<item>_S']})

In [7]:
target_items_binding 

defaultdict(<function __main__.<lambda>()>,
            {'Survived': ['Survived_<item>_0', 'Survived_<item>_1']})

### Stop List
The items from the same attribute can not be in the same itemset

In [8]:
import itertools
stop_list = []
for items in stable_items_binding.values():
    for stop_couple in itertools.combinations(items, 2):
        stop_list.append(tuple(stop_couple))
for items in flexible_items_binding.values():
    for stop_couple in itertools.combinations(items, 2):
        stop_list.append(tuple(stop_couple))
for items in target_items_binding.values():
    for stop_couple in itertools.combinations(items, 2):
        stop_list.append(tuple(stop_couple))

### Split table
Split based on the target

In [9]:
frames = {}
for item in target_items_binding[target]:
    mask = data[item]==1
    frames[item] = data[mask]
frames

{'Survived_<item>_0':    Sex_<item>_F  Sex_<item>_M  Age_<item>_O  Age_<item>_Y  Class_<item>_1  \
 2             0             1             1             0               0   
 3             0             1             0             1               0   
 6             1             0             0             1               0   
 
    Class_<item>_2  Embarked_<item>_C  Embarked_<item>_S  Survived_<item>_0  \
 2               1                  0                  1                  1   
 3               1                  1                  0                  1   
 6               1                  1                  0                  1   
 
    Survived_<item>_1  
 2                  0  
 3                  0  
 6                  0  ,
 'Survived_<item>_1':    Sex_<item>_F  Sex_<item>_M  Age_<item>_O  Age_<item>_Y  Class_<item>_1  \
 0             0             1             0             1               1   
 1             1             0             0             1               

### Target States

In [10]:
unwanted_state = target + '_<item>_' + str(wanted_change_in_target[0])
wanted_state = target + '_<item>_' + str(wanted_change_in_target[1])

# APRIORI
### Generates candidates
Generates canidates and also mines classification rules

In [11]:
action_rules = []
classification_rules = defaultdict(lambda: {'wanted': [], 'unwanted': []})
    

def generate_candidates(attribute_prefix, itemset_prefix, stable_items_binding, flexible_items_binding, unwanted_mask, wanted_mask, actionable_attributes=0):
    K = len(itemset_prefix) + 1
    reduced_stable_items_binding = stable_items_binding.copy()
    reduced_flexible_items_binding = flexible_items_binding.copy()
    new_prefixes = []

    number_of_stable_attributes = len(stable_items_binding) - (min_stable_attributes - K)
    
    if unwanted_mask is None:
        unwanted_frame = frames[unwanted_state]
        wanted_frame = frames[wanted_state]
    else:
        #unwanted_frame = frames[unwanted_state] * unwanted_mask
        unwanted_frame = frames[unwanted_state].multiply(unwanted_mask, axis="index")
        #wanted_frame = frames[wanted_state] * wanted_mask
        wanted_frame = frames[wanted_state].multiply(wanted_mask, axis="index")
    
    for i, (attribute, items) in enumerate(stable_items_binding.items()):
        if i == number_of_stable_attributes:
            break
        for item in items.copy():
            
            break_loop = False
            cand_prefix = itemset_prefix + (item, )
            for stop in stop_list:
                start_comparison = len(cand_prefix)-len(stop)
                if start_comparison >=0:
                    if cand_prefix[start_comparison:] == stop:
                        break_loop = True
                        break
            if break_loop:
                continue
            print('SUPPORT')
            print(cand_prefix)
            
            unwanted_support = unwanted_frame[item].sum()
            wanted_support = wanted_frame[item].sum()
            if unwanted_support < min_unwanted_support or wanted_support < min_wanted_support:
                reduced_stable_items_binding[attribute].remove(item)
            else:
                new_prefixes.append(item)
            
    if K > min_stable_attributes:

        number_of_flexible_attributes = len(flexible_items_binding) - (min_flexible_attributes - actionable_attributes)
        print("N Flex")
        print(number_of_flexible_attributes)
        
        for i, (attribute, items) in enumerate(flexible_items_binding.items()):  
            
            break_loop = False
            cand_prefix = itemset_prefix + (attribute, )
            for stop in stop_list:
                start_comparison = len(cand_prefix)-len(stop)
                if start_comparison >=0:
                    if cand_prefix[start_comparison:] == stop:
                        print('STOP')
                        print(cand_prefix)
                        break_loop = True
                        break
            if break_loop:
                continue
            
            unwanted_states = []
            wanted_states = []
            for item in items.copy():    
                print('SUPPORT')
                print(itemset_prefix + (item, ))
                
                unwanted_support = unwanted_frame[item].sum()
                wanted_support = wanted_frame[item].sum()
                
                print(unwanted_support)
                print(wanted_support)
                
                # is unwanted
                if wanted_support + unwanted_support == 0:
                    unwanted_conf = 0
                else:
                    unwanted_conf = unwanted_support/(wanted_support + unwanted_support)
                if unwanted_support >= min_unwanted_support: # and unwanted_conf >= min_unwanted_confidence:
                    unwanted_states.append({'item': item, 'support': unwanted_support, 'confidence':unwanted_conf})
                # is wanted
                if wanted_support + unwanted_support == 0:
                    wanted_conf = 0
                else:
                    wanted_conf = wanted_support/(wanted_support + unwanted_support) 
                    
                print('conf')
                print(unwanted_conf)
                print(wanted_conf)
                    
                if wanted_support >= min_wanted_support: # and wanted_conf >= min_wanted_confidence:
                    wanted_states.append({'item': item, 'support': wanted_support, 'confidence': wanted_conf})    
            if actionable_attributes == 0 and (len(unwanted_states) == 0 or len(wanted_states) == 0):
                print('DEL---------------')
                print(attribute)
                del reduced_flexible_items_binding[attribute]
                stop_list.append(itemset_prefix + (attribute, ))
            else:
                print('cand--------------------')
                print(i)
                print(number_of_flexible_attributes)
                print(item)
                print('')
                if i < number_of_flexible_attributes:
                    for item in items.copy(): 
                        new_prefixes.append(item)
                if actionable_attributes + 1 >= min_flexible_attributes:
                    new_attribute_prefix = attribute_prefix + (attribute, )
                    for unwanted_item in unwanted_states:
                        new_itemset_prefix = itemset_prefix + (unwanted_item['item'], )
                        classification_rules[new_attribute_prefix]['unwanted'].append({
                                             'itemset': new_itemset_prefix,  
                                             'support': unwanted_item['support'],
                                             'confidence': unwanted_item['confidence'],
                                             'target': wanted_change_in_target[0]
                                            })
                    for wanted_item in wanted_states:
                        new_itemset_prefix = itemset_prefix + (wanted_item['item'], )
                        classification_rules[new_attribute_prefix]['wanted'].append({
                                             'itemset':new_itemset_prefix, 
                                             'support': wanted_item['support'],
                                             'confidence': wanted_item['confidence'],
                                             'target': wanted_change_in_target[1]
                                            })
    
    new_candidates = []
    print('PREFIXES------')
    print(new_prefixes)
    print('BIND')
    print(reduced_flexible_items_binding.items())
    for new_prefix in new_prefixes:
        is_in_tree = False
        new_stable_items_binding = defaultdict(lambda: [])
        new_flexible_items_binding = defaultdict(lambda: [])
        new_actionable_attributes = actionable_attributes
        
        for attribute, items in reduced_stable_items_binding.items():
            for item in items:
                if is_in_tree:
                    new_stable_items_binding[attribute].append(item)
                if item == new_prefix:
                    is_in_tree = True
        for attribute, items in reduced_flexible_items_binding.items():
            for item in items:
                if is_in_tree:
                    new_flexible_items_binding[attribute].append(item)
                if item == new_prefix:
                    is_in_tree = True
                    new_actionable_attributes += 1
        new_itemset_prefix = itemset_prefix + (new_prefix,)
        if new_actionable_attributes > 0:
            new_attribute_prefix = attribute_prefix + (new_prefix[:new_prefix.index('_<item>_')], )
        else:
            new_attribute_prefix = attribute_prefix + (new_prefix, )
        new_candidates.append({
                               'attribute_prefix': new_attribute_prefix,
                               'itemset_prefix': new_itemset_prefix,
                               'stable_items_binding': new_stable_items_binding,
                               'flexible_items_binding': new_flexible_items_binding,
                               'unwanted_mask': unwanted_frame[new_prefix],
                               'wanted_mask': wanted_frame[new_prefix],
                               'actionable_attributes': new_actionable_attributes,
                              })
    return new_candidates



### Generates Action Rules

In [12]:
def generate_action_rules():
    for attribute_prefix, rules in classification_rules.items():            
        for wanted_rule in rules['wanted']:
            if wanted_rule['confidence'] <  min_wanted_confidence:
                continue
            for unwanted_rule in rules['unwanted']:
                if unwanted_rule['confidence'] <  min_unwanted_confidence:
                    continue
                action_rules.append({'unwanted': unwanted_rule, 'wanted': wanted_rule})

# Prune tree

In [13]:
def prune_tree(K):
    print('PRUNE-----------')
    print(K)
    for attribute_prefix, rules in classification_rules.items():
        print('----------prune')
        print(K)
        print(attribute_prefix)
        if K == len(attribute_prefix):
            if len(rules['wanted']) < 0 or len(rules['unwanted']) < 0:
                print('PRUNE')
                print(attribute_prefix)
                stop_list.append(attribute_prefix)    

### Apriori iterations

In [14]:
def ar_apriori():
    candidates_queue = [{
                         'attribute_prefix': tuple(),
                         'itemset_prefix':tuple(), 
                         'stable_items_binding': stable_items_binding, 
                         'flexible_items_binding': flexible_items_binding,
                         'unwanted_mask': None,
                         'wanted_mask': None,
                         'actionable_attributes':0
                        }]
    K = 0
    while len(candidates_queue)>0:
        candidate = candidates_queue.pop(0)
        if len(candidate['attribute_prefix']) > K:
            K+=1
            prune_tree(K)
        print('')
        print('////////////CAND')
        print(candidate['itemset_prefix'])
        print(candidate['flexible_items_binding'])
        print(candidate['actionable_attributes'])
        print('')
        new_candidates = generate_candidates(**candidate)
        candidates_queue += new_candidates
    generate_action_rules()

print('ITEMSET - counting support')
ar_apriori()

ITEMSET - counting support

////////////CAND
()
defaultdict(<function <lambda> at 0x000001BD6E0764C0>, {'Class': ['Class_<item>_1', 'Class_<item>_2'], 'Embarked': ['Embarked_<item>_C', 'Embarked_<item>_S']})
0

SUPPORT
('Sex_<item>_F',)
SUPPORT
('Sex_<item>_M',)
PREFIXES------
['Sex_<item>_F', 'Sex_<item>_M']
BIND
dict_items([('Class', ['Class_<item>_1', 'Class_<item>_2']), ('Embarked', ['Embarked_<item>_C', 'Embarked_<item>_S'])])
PRUNE-----------
1

////////////CAND
('Sex_<item>_F',)
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD6E092430>, {'Class': ['Class_<item>_1', 'Class_<item>_2'], 'Embarked': ['Embarked_<item>_C', 'Embarked_<item>_S']})
0

SUPPORT
('Sex_<item>_F', 'Age_<item>_O')
SUPPORT
('Sex_<item>_F', 'Age_<item>_Y')
PREFIXES------
['Age_<item>_Y']
BIND
dict_items([('Class', ['Class_<item>_1', 'Class_<item>_2']), ('Embarked', ['Embarked_<item>_C', 'Embarked_<item>_S'])])

////////////CAND
('Sex_<item>_M',)
defaultdict(<function generate_candidates.

### Action rules

In [15]:
print('ACTION RULES')
print(action_rules)

ACTION RULES
[{'unwanted': {'itemset': ('Sex_<item>_F', 'Age_<item>_Y', 'Class_<item>_2'), 'support': 1, 'confidence': 1.0, 'target': 0}, 'wanted': {'itemset': ('Sex_<item>_F', 'Age_<item>_Y', 'Class_<item>_1'), 'support': 2, 'confidence': 1.0, 'target': 1}}]


# Compare new algorithm with ActionRulesDiscovery package

In [16]:
import pandas as pd
from actionrules.actionRulesDiscovery import ActionRulesDiscovery
dataFrame = pd.read_csv("titanic.csv", sep=";")
dataFrame.head()

ID                  Age Embarked       Fare  Pclass     Sex  Survived
0   1  <16.13336;32.10002)        S  very high     1.0  female       1.0
1   2    <0.1667;16.13336)        S  very high     1.0    male       1.0
2   3    <0.1667;16.13336)        S  very high     1.0  female       0.0
3   4  <16.13336;32.10002)        S  very high     1.0    male       0.0
4   5  <16.13336;32.10002)        S  very high     1.0  female       0.0

### ActionRulesDiscovery package

In [17]:
actionRulesDiscovery = ActionRulesDiscovery()
actionRulesDiscovery.load_pandas(dataFrame)
actionRulesDiscovery.fit(stable_attributes = ["Age", "Sex"],
                         flexible_attributes = ["Embarked", "Fare", "Pclass"],
                         consequent = "Survived",
                         conf=55,
                         supp=3,
                         desired_classes = ["1.0"],
                         is_strict_flexible = False
                         )

In [18]:
for rule in actionRulesDiscovery.get_action_rules_representation():
    print(rule)
    print(" ")

r = [(Age: <16.13336;32.10002)) ∧ (Embarked: s → c) ] ⇒ [Survived: 0.0 → 1.0] with support: 0.04198473282442748, confidence: 0.40990990990991, uplift: 0.08757421543681088.
 
r = [(Age: <16.13336;32.10002)) ∧ (Pclass: 3.0 → 1.0) ] ⇒ [Survived: 0.0 → 1.0] with support: 0.04732824427480916, confidence: 0.5261127825349071, uplift: 0.10257085197859087.
 
r = [(Age: <16.13336;32.10002)) ∧ (Fare: avg → very high) ] ⇒ [Survived: 0.0 → 1.0] with support: 0.044274809160305344, confidence: 0.43256997455470736, uplift: 0.031552162849872764.
 
r = [(Age: <16.13336;32.10002)) ∧ (Pclass: 2.0 → 1.0) ] ⇒ [Survived: 0.0 → 1.0] with support: 0.04732824427480916, confidence: 0.42040850078557845, uplift: 0.032104939896463985.
 
r = [(Age: <16.13336;32.10002)) ∧ (Fare: avg → very high)  ∧ (Pclass: 2.0 → 1.0) ] ⇒ [Survived: 0.0 → 1.0] with support: 0.03969465648854962, confidence: 0.46254681647940077, uplift: 0.02463952502120441.
 
r = [(Age: <16.13336;32.10002)) ∧ (Fare: very low → very high) ] ⇒ [Survived:

### AR-APRIORI

In [19]:
action_rules = []
classification_rules = defaultdict(lambda: {'wanted': [], 'unwanted': []})
# Data
data = pd.get_dummies(dataFrame, sparse=False, columns=dataFrame.columns, prefix_sep='_<item>_')
# Input
stable_attributes = ['Age','Sex']
flexible_attributes = ["Embarked", "Fare", "Pclass"]
target = 'Survived'
wanted_change_in_target = ['0.0', '1.0']
min_stable_attributes = 1
min_flexible_attributes = 1 #min 1
min_unwanted_support = 39
min_unwanted_confidence = 0.55 #min 0.5
min_wanted_support = 39
min_wanted_confidence = 0.55 #min 0.5


# Bindings
from collections import defaultdict

stable_items_binding = defaultdict(lambda: [])
flexible_items_binding = defaultdict(lambda: [])
target_items_binding = defaultdict(lambda: [])

for col in data.columns:
    is_continue = False
    # stable
    for attribute in stable_attributes:
        if col.startswith(attribute+'_<item>_'):
            stable_items_binding[attribute].append(col)
            is_continue = True
            break
    if is_continue is True:
        continue
    # flexible    
    for attribute in flexible_attributes:
        if col.startswith(attribute+'_<item>_'):
            flexible_items_binding[attribute].append(col)
            is_continue = True
            break
    if is_continue is True:
        continue
    # target    
    if col.startswith(target+'_<item>_'):
        target_items_binding[target].append(col)     

In [20]:
import itertools
stop_list = []
for items in stable_items_binding.values():
    for stop_couple in itertools.combinations(items, 2):
        stop_list.append(tuple(stop_couple))
for items in flexible_items_binding.values():
    for stop_couple in itertools.combinations(items, 2):
        stop_list.append(tuple(stop_couple))
for items in target_items_binding.values():
    for stop_couple in itertools.combinations(items, 2):
        stop_list.append(tuple(stop_couple))

In [21]:
frames = {}
for item in target_items_binding[target]:
    mask = data[item]==1
    frames[item] = data[mask]

In [22]:
unwanted_state = target + '_<item>_' + str(wanted_change_in_target[0])
wanted_state = target + '_<item>_' + str(wanted_change_in_target[1])

In [23]:
print('ITEMSET - counting support')
ar_apriori()

ITEMSET - counting support

////////////CAND
()
defaultdict(<function <lambda> at 0x000001BD6E0E2AF0>, {'Embarked': ['Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S'], 'Fare': ['Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Fare_<item>_very low'], 'Pclass': ['Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0']})
0

SUPPORT
('Age_<item>_<0.1667;16.13336)',)
SUPPORT
('Age_<item>_<16.13336;32.10002)',)
SUPPORT
('Age_<item>_<32.10002;48.06668)',)
SUPPORT
('Age_<item>_<48.06668;64.03334)',)
SUPPORT
('Age_<item>_<64.03334;80>',)
SUPPORT
('Sex_<item>_female',)
SUPPORT
('Sex_<item>_male',)
PREFIXES------
['Age_<item>_<0.1667;16.13336)', 'Age_<item>_<16.13336;32.10002)', 'Age_<item>_<32.10002;48.06668)', 'Age_<item>_<48.06668;64.03334)', 'Sex_<item>_female', 'Sex_<item>_male']
BIND
dict_items([('Embarked', ['Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S']), ('Fare', ['Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<ite

33
20
conf
0.6226415094339622
0.37735849056603776
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_male', 'Embarked_<item>_Q')
9
2
conf
0.8181818181818182
0.18181818181818182
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_male', 'Embarked_<item>_S')
232
43
conf
0.8436363636363636
0.15636363636363637
cand--------------------
0
2
Embarked_<item>_S

SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_male', 'Fare_<item>_avg')
67
9
conf
0.881578947368421
0.11842105263157894
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_male', 'Fare_<item>_higher')
26
9
conf
0.7428571428571429
0.2571428571428571
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_male', 'Fare_<item>_lower')
89
13
conf
0.8725490196078431
0.12745098039215685
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_male', 'Fare_<item>_very high')
28
13
conf
0.6829268292682927
0.3170731707317073
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_male', 'Fare_<item>_very low')
64
21
conf
0.75294117

26
13
conf
0.6666666666666666
0.3333333333333333
SUPPORT
('Age_<item>_<32.10002;48.06668)', 'Fare_<item>_avg', 'Pclass_<item>_3.0')
12
8
conf
0.6
0.4
cand--------------------
1
2
Pclass_<item>_3.0

PREFIXES------
['Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Fare_<item>_very low', 'Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0']
BIND
dict_items([('Fare', ['Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Fare_<item>_very low']), ('Pclass', ['Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0'])])

////////////CAND
('Age_<item>_<32.10002;48.06668)', 'Fare_<item>_higher')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD6E48F700>, {'Fare': ['Fare_<item>_lower', 'Fare_<item>_very high', 'Fare_<item>_very low'], 'Pclass': ['Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0']})
1

N Flex
2
SUPPORT
('Age_<item>_<32.10002;48.06668)', 'Fare_<item>_higher', 'Fare_<item>_lower')
0
0
conf
0
0
SUPPO

////////////CAND
('Sex_<item>_male', 'Fare_<item>_very low')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD6E4801F0>, {'Pclass': ['Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0']})
1

N Flex
1
SUPPORT
('Sex_<item>_male', 'Fare_<item>_very low', 'Pclass_<item>_1.0')
7
1
conf
0.875
0.125
SUPPORT
('Sex_<item>_male', 'Fare_<item>_very low', 'Pclass_<item>_2.0')
6
0
conf
1.0
0.0
SUPPORT
('Sex_<item>_male', 'Fare_<item>_very low', 'Pclass_<item>_3.0')
152
29
conf
0.8397790055248618
0.16022099447513813
cand--------------------
0
1
Pclass_<item>_3.0

PREFIXES------
['Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0']
BIND
dict_items([('Pclass', ['Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0'])])
PRUNE-----------
3
----------prune
3
('Age_<item>_<0.1667;16.13336)', 'Embarked')
----------prune
3
('Age_<item>_<16.13336;32.10002)', 'Embarked')
----------prune
3
('Age_<item>_<16.13336;32.10002)', 'Fare')
----------prune
3
('Age_<ite

1
3
Pclass_<item>_3.0

PREFIXES------
['Fare_<item>_very high', 'Fare_<item>_very low', 'Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0']
BIND
dict_items([('Fare', ['Fare_<item>_very high', 'Fare_<item>_very low']), ('Pclass', ['Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0'])])

////////////CAND
('Age_<item>_<16.13336;32.10002)', 'Embarked_<item>_C', 'Fare_<item>_very high')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD6E24EAF0>, {'Fare': ['Fare_<item>_very low'], 'Pclass': ['Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0']})
2

N Flex
3
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Embarked_<item>_C', 'Fare_<item>_very high', 'Fare_<item>_very low')
0
0
conf
0
0
cand--------------------
0
3
Fare_<item>_very low

SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Embarked_<item>_C', 'Fare_<item>_very high', 'Pclass_<item>_1.0')
7
29
conf
0.19444444444444445
0.8055555555555556
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Embarke

...

('Age_<item>_<32.10002;48.06668)', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Pclass_<item>_1.0', 'Pclass_<item>_3.0')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD01F64700>, {})
9

N Flex
8
PREFIXES------
[]
BIND
dict_items([])

////////////CAND
('Age_<item>_<32.10002;48.06668)', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD12ECB310>, {})
9

N Flex
8
PREFIXES------
[]
BIND
dict_items([])

////////////CAND
('Age_<item>_<32.10002;48.06668)', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very low', 'Pclass_<item>_1.0', 'Pclass_<item>_2.0')
defaultd

N Flex
8
PREFIXES------
[]
BIND
dict_items([])

////////////CAND
('Sex_<item>_male', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Pclass_<item>_1.0', 'Pclass_<item>_2.0')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD12ECBF70>, {'Pclass': ['Pclass_<item>_3.0']})
9

N Flex
9
SUPPORT
('Sex_<item>_male', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0')
0
0
conf
0
0
cand--------------------
0
9
Pclass_<item>_3.0

PREFIXES------
['Pclass_<item>_3.0']
BIND
dict_items([('Pclass', ['Pclass_<item>_3.0'])])

////////////CAND
('Sex_<item>_male', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Pclass_<ite

N Flex
9
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_female', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Fare_<item>_very low', 'Pclass_<item>_1.0', 'Pclass_<item>_2.0')
0
0
conf
0
0
SUPPORT
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_female', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Fare_<item>_very low', 'Pclass_<item>_1.0', 'Pclass_<item>_3.0')
0
0
conf
0
0
cand--------------------
0
9
Pclass_<item>_3.0

PREFIXES------
['Pclass_<item>_2.0', 'Pclass_<item>_3.0']
BIND
dict_items([('Pclass', ['Pclass_<item>_2.0', 'Pclass_<item>_3.0'])])

////////////CAND
('Age_<item>_<16.13336;32.10002)', 'Sex_<item>_female', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', '


N Flex
9
PREFIXES------
[]
BIND
dict_items([])

////////////CAND
('Age_<item>_<16.13336;32.10002)', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Fare_<item>_very low', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD712809D0>, {})
10

N Flex
9
PREFIXES------
[]
BIND
dict_items([])

////////////CAND
('Age_<item>_<16.13336;32.10002)', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD73527EE0>, {})
10

N Flex
9
PREFIXES------
[]
BIND
dict_items([])

////////////CAND
('Age_<item>_<16.13336;32.10002)', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Far

N Flex
10
PREFIXES------
[]
BIND
dict_items([])

////////////CAND
('Age_<item>_<32.10002;48.06668)', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Fare_<item>_very low', 'Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD73527F70>, {})
11

N Flex
10
PREFIXES------
[]
BIND
dict_items([])

////////////CAND
('Sex_<item>_male', 'Embarked_<item>_C', 'Embarked_<item>_Q', 'Embarked_<item>_S', 'Fare_<item>_avg', 'Fare_<item>_higher', 'Fare_<item>_lower', 'Fare_<item>_very high', 'Fare_<item>_very low', 'Pclass_<item>_1.0', 'Pclass_<item>_2.0', 'Pclass_<item>_3.0')
defaultdict(<function generate_candidates.<locals>.<lambda> at 0x000001BD73527160>, {})
11

N Flex
10
PREFIXES------
[]
BIND
dict_items([])
PRUNE-----------
13
----------prune
13
('Age_<item>_<0.1667;16.13336)', 'Embarked')
----------prune
13
('Ag

In [24]:
print('ACTION RULES')
for rule in action_rules:
    print(rule)
    print(" ")

ACTION RULES
{'unwanted': {'itemset': ('Age_<item>_<16.13336;32.10002)', 'Embarked_<item>_S'), 'support': 273, 'confidence': 0.6707616707616708, 'target': '0.0'}, 'wanted': {'itemset': ('Age_<item>_<16.13336;32.10002)', 'Embarked_<item>_C'), 'support': 55, 'confidence': 0.6111111111111112, 'target': '1.0'}}
 
{'unwanted': {'itemset': ('Age_<item>_<16.13336;32.10002)', 'Fare_<item>_avg'), 'support': 85, 'confidence': 0.648854961832061, 'target': '0.0'}, 'wanted': {'itemset': ('Age_<item>_<16.13336;32.10002)', 'Fare_<item>_very high'), 'support': 58, 'confidence': 0.6666666666666666, 'target': '1.0'}}
 
{'unwanted': {'itemset': ('Age_<item>_<16.13336;32.10002)', 'Fare_<item>_lower'), 'support': 108, 'confidence': 0.8059701492537313, 'target': '0.0'}, 'wanted': {'itemset': ('Age_<item>_<16.13336;32.10002)', 'Fare_<item>_very high'), 'support': 58, 'confidence': 0.6666666666666666, 'target': '1.0'}}
 
{'unwanted': {'itemset': ('Age_<item>_<16.13336;32.10002)', 'Fare_<item>_very low'), 'sup

In [25]:
print(len(action_rules))

15
